# 감성분석

In [2]:
# 영화 리뷰 데이터 불러오기
import pandas as pd

review_df = pd.read_csv('./movie_text_data/ratings.txt', header=0, sep="\t", quoting=3)
review_df.head(3)

id                                           document  label
0  8112052                                어릴때보고 지금다시봐도 재밌어요ㅋㅋ      1
1  8132799  디자인을 배우는 학생으로, 외국디자이너와 그들이 일군 전통을 통해 발전해가는 문화산...      1
2  4655635               폴리스스토리 시리즈는 1부터 뉴까지 버릴께 하나도 없음.. 최고.      1

In [3]:
# 전처리
import re


review_df['document'] = review_df['document'].apply(lambda x : re.sub(pattern="[^ㄱ-ㅎ 가-힣 a-z A-Z]", repl=" ", string=str(x)))

review_df.head(10)

id                                           document  label
0   8112052                                어릴때보고 지금다시봐도 재밌어요ㅋㅋ      1
1   8132799  디자인을 배우는 학생으로  외국디자이너와 그들이 일군 전통을 통해 발전해가는 문화산...      1
2   4655635               폴리스스토리 시리즈는  부터 뉴까지 버릴께 하나도 없음   최고       1
3   9251303  와   연기가 진짜 개쩔구나   지루할거라고 생각했는데 몰입해서 봤다   그래 이런...      1
4  10067386                        안개 자욱한 밤하늘에 떠 있는 초승달 같은 영화       1
5   2190435                      사랑을 해본사람이라면 처음부터 끝까지 웃을수 있는영화      1
6   9279041                                   완전 감동입니다 다시봐도 감동      1
7   7865729                        개들의 전쟁  나오나요  나오면  빠로 보고 싶음      1
8   7477618                                                  굿      1
9   9250537                                     바보가 아니라 병 쉰 인듯      1

In [4]:
#test - train set 나누기

from sklearn.model_selection import train_test_split

class_df = review_df['label']
feature_df = review_df.drop(['id', 'label'], axis=1, inplace=False)

X_train, X_test, y_train, y_test = train_test_split(feature_df, class_df, test_size=0.3, random_state=156)

X_train.shape, X_test.shape


                                                 document
141220                                     이름 함부러 짓는거 아니다
165836                                    점도 아깝다 쓰레기같은 영화
570                          고어물론 최고다   기발한연출력   맘에들었음   
188540                                       이건 뭐 무섭지도 않고
183247  다시는 중국이랑 같이 접목하지마라    쪽팔림 진심    중국을데려다가 이렇게밖에못...
...                                                   ...
22047                         ㅋㅋㅋ 그래도 평점이 너무 낮다  육점은 받아야지
9938                      전체적인 구성은 좋았지만 세밀한 디테일이 좀 부족한 영화
13305   누가 b급영화는 전부다 쓰레기라고 하는가 이렇게도 만들수있는데 그런놈들은 뭐 폭발펑...
127040                                          감독의 역량 부족
32336                                             생동감 그자체

[60000 rows x 1 columns]


In [15]:
# 로지스틱 회귀 + CountVectorize

from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, roc_auc_score

pipeline = Pipeline([
    ('cnt_vect', CountVectorizer(ngram_range=(1,2))),
    ('lr_clf',LogisticRegression(C=10))

])

pipeline.fit(X_train['document'], y_train)
pred = pipeline.predict(X_test['document'])
pred_probs = pipeline.predict_proba(X_test['document'])[:,1]

print('예측 정확도는 {0:.4f}, ROC_AUC는 {1:.4f}'.format(accuracy_score(y_test, pred), roc_auc_score(y_test, pred_probs)))

cnt = 0
for review in X_test['document']:
    if pred[cnt] == 1:
        sentiment = 'positive'
    else:
        sentiment = 'negative'

    cnt += 1
    if cnt == 100:
        break

    print('댓글 :{0} 는 {1}로 예상됩니다'.format(review, sentiment))


예측 정확도는 0.8116, ROC_AUC는 0.9028
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 positive로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개웃기네ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ 는 negative로 예상됩니다
댓글 : 다 똑같이 생겨가지고 개

In [37]:
# 로지스틱 회귀 + TfidfVectorize

pipeline = Pipeline([
    ('tfidf_vect', TfidfVectorizer(ngram_range=(1,2))),
    ('lr_clf',LogisticRegression(C=10))

])

pipeline.fit(X_train['document'], y_train)
pred = pipeline.predict(X_test['document'])
pred_probs = pipeline.predict_proba(X_test['document'])[:,1]

print('예측 정확도는 {0:.4f}, ROC_AUC는 {1:.4f}'.format(accuracy_score(y_test, pred), roc_auc_score(y_test, pred_probs)))

예측 정확도는 0.8150, ROC_AUC는 0.9054


In [14]:
# 유튜브 댓글 데이터 불러오기

with open('./crawling_result_text/gamst_comments.txt', mode='rt', encoding='utf-8') as f:
    strings = f.read()

strings = re.sub(pattern='[^ㄱ-ㅎ 가-힣 a-z A-Z \n]', repl='', string=strings)
comment_list = strings.split('\n')

pred_comment = pipeline.predict(comment_list)

cnt = 0
for comment in comment_list:
    if pred_comment[cnt] == 1:
        sentiment = 'positive'
    else:
        sentiment = 'negative'

    cnt += 1

    print('댓글 :{0} 는 {1}로 예상됩니다'.format(comment, sentiment))


댓글 :영상 좋아요댓글 한번씩 부탁드립니다는 positive로 예상됩니다
댓글 :He is JJASTHIS는 positive로 예상됩니다
댓글 :HE IS NOT CHANGMO는 positive로 예상됩니다
댓글 :HE IS TALMO는 positive로 예상됩니다
댓글 :He is Talmoalto는 positive로 예상됩니다
댓글 :Bring rap JJASTHIS는 negative로 예상됩니다
댓글 : He Is gamshebellom는 positive로 예상됩니다
댓글 :He is CODE GAMST는 positive로 예상됩니다
댓글 :THISISZZASTHIS는 negative로 예상됩니다
댓글 : 여긴 진짜 개잘했네 ㅋㅋㅋㅋ는 positive로 예상됩니다
댓글 : he is punchline king는 positive로 예상됩니다
댓글 :보여줬지는 negative로 예상됩니다
댓글 :yo는 negative로 예상됩니다
댓글 :shut the fxxk a man는 positive로 예상됩니다
댓글 :ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ는 negative로 예상됩니다
댓글 :느슨해진 한국힙합에 긴장감을 주는것 같다는 positive로 예상됩니다
댓글 :  우결단의 인생 감스트는 positive로 예상됩니다
댓글 : 여기서부터 ㅈㄴ노래 좋음는 positive로 예상됩니다
댓글 : 개 중독된다 그냥 짜쓰디스 레게노는 negative로 예상됩니다
댓글 :  지렸다 는 positive로 예상됩니다
댓글 :He is SMTM  WINNER는 positive로 예상됩니다
댓글 :  박자 맞는거 소름이누ㄷㄷ는 negative로 예상됩니다
댓글 :아니 프리스타일인데 랩을 이렇게 잘한다고ㅋㅋㅋㅋㅋ 그냥 말하는 것보다 더 잘하는데 ㅋㅋ 진짜 놀랬다는 negative로 예상됩니다
댓글 : 말하면서 들어가는거 우원재 급인데 킹스트는 negative로 예상됩니다
댓글 :He is a korean는 positive로 예상됩니다
댓글 :He 